### Cold Start Problem

In the previous notebook, you learned about the **Cold Start Problem** first hand. In cases where you are introduced to a new user or new movie, collaborative flitering is not helpful as a technique to make predictions.

Instead, you will need to use one of the techniques from the previous lesson like content based recommendations for new items or rank based recommendations for new users.  

As a final step to completing out our recommendation system, we will build in these edge cases. Run the cell below to get started.

### Matrix Factorization - Collaborative Filtering Where Possible

Notice the following information is available by running the below cell:

`1.` **reviews** - a dataframe of reviews

`2.` **movies** - a dataframe of movies

`3.` **create_train_test** - a function for creating the training and validation datasets

`4.` **predict_rating** - a function that takes a user and movie and gives a prediction using FunkSVD

`5.` **train_df** and **val_df** - the training and test datasets used in the previous notebook

`6.` **user_mat** and **movie_mat** - the u and v matrices from FunkSVD

`7.` **train_data_df** - a user-movie matrix with ratings where available.  FunkSVD was performed on this matrix

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
import pickle

# Read in the datasets
movies = pd.read_csv('data/movies_clean.csv')
reviews = pd.read_csv('data/reviews_clean.csv')

del movies['Unnamed: 0']
del reviews['Unnamed: 0']

def create_train_test(reviews, order_by, training_size, testing_size):
    '''    
    INPUT:
    reviews - (pandas df) dataframe to split into train and test
    order_by - (string) column name to sort by
    training_size - (int) number of rows in training set
    testing_size - (int) number of columns in the test set
    
    OUTPUT:
    training_df -  (pandas df) dataframe of the training set
    validation_df - (pandas df) dataframe of the test set
    '''
    reviews_new = reviews.sort_values(order_by)
    training_df = reviews_new.head(training_size)
    validation_df = reviews_new.iloc[training_size:training_size+testing_size]
    
    return training_df, validation_df

def predict_rating(user_matrix, movie_matrix, user_id, movie_id):
    '''
    INPUT:
    user_matrix - user by latent factor matrix
    movie_matrix - latent factor by movie matrix
    user_id - the user_id from the reviews df
    movie_id - the movie_id according the movies df
    
    OUTPUT:
    pred - the predicted rating for user_id-movie_id according to FunkSVD
    '''
    # Create series of users and movies in the right order
    user_ids_series = np.array(train_data_df.index)
    movie_ids_series = np.array(train_data_df.columns)
    
    # User row and Movie Column
    user_row = np.where(user_ids_series == user_id)[0][0]
    movie_col = np.where(movie_ids_series == movie_id)[0][0]
    
    # Take dot product of that row and column in U and V to make prediction
    pred = np.dot(user_matrix[user_row, :], movie_matrix[:, movie_col])
    
    return pred

# Use our function to create training and test datasets
train_df, val_df = create_train_test(reviews, 'date', 8000, 2000)

# Create user-by-item matrix - this will keep track of order of users and movies in u and v
train_user_item = train_df[['user_id', 'movie_id', 'rating', 'timestamp']]
train_data_df = train_user_item.groupby(['user_id', 'movie_id'])['rating'].max().unstack()
train_data_np = np.array(train_data_df)

# Read in user and movie matrices
user_file = open("user_matrix", 'rb')
user_mat = pickle.load(user_file)
user_file.close()

movie_file = open("movie_matrix", 'rb')
movie_mat = pickle.load(movie_file)
movie_file.close()

/home/randomwalk10/anaconda3/envs/aind/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/home/randomwalk10/anaconda3/envs/aind/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


### Validating Predictions

Unfortunately, you weren't able to make predictions on every user-movie combination in the test set, as some of these users or movies were new.  

However, you can validate your predictions for the user-movie pairs that do exist in the user_mat and movie_mat matrices.  

`1.` Complete the function below to see how far off we were on average across all of the predicted ratings.

In [29]:
np.sum(reviews.rating==0)

191

In [38]:
max(int(10.5), -1)

10

In [39]:
def validation_comparison(val_df, user_mat=user_mat, movie_mat=movie_mat):
    '''
    INPUT:
    val_df - the validation dataset created in the third cell above
    user_mat - U matrix in FunkSVD
    movie_mat - V matrix in FunkSVD
        
    OUTPUT:
    rmse - RMSE of how far off each value is from it's predicted value
    perc_rated - percent of predictions out of all possible that could be rated
    actual_v_pred - a 10 x 10 grid with counts for actual vs predicted values
    preds - (list) predictions for any user-movie pairs where it was possible to make a prediction
    acts - (list) actual values for any user-movie pairs where it was possible to make a prediction
    '''
    num_user = val_df.shape[0] # number of users
    preds = []
    acts = []
    actual_v_pred = np.zeros((10, 10))
    rmse = 0
    for i in range(num_user):
        user_id = val_df.iloc[i]['user_id']
        movie_id = val_df.iloc[i]['movie_id']
        true_val = val_df.iloc[i]['rating']
        try:
            pred_val = predict_rating(user_mat, movie_mat, user_id, movie_id)
            preds.append(pred_val)
            acts.append(true_val)
            rmse += (true_val-pred_val)**2
            actual_v_pred[max(true_val-1, 0)][max(int(pred_val-1), 0)] += 1
            pass
        except:
            pass
    perc_rated = len(preds) / num_user
    rmse = np.sqrt(rmse/num_user)
    return rmse, perc_rated, actual_v_pred, preds, acts

In [40]:
# How well did we do? # Make some plots and calculate some statistics to 
# understand how well this technique is working
rmse, perc_rated, actual_v_pred, preds, acts = validation_comparison(val_df, user_mat, movie_mat)

In [41]:
print("rmse %f, perc_rated %f" % (rmse, perc_rated))

rmse 1.418584, perc_rated 0.479500


In [42]:
print(actual_v_pred)

[[ 1.  1.  1.  1.  1.  3.  1.  1.  2.  0.]
 [ 1.  2.  0.  0.  2.  1.  0.  0.  1.  0.]
 [ 0.  1.  1.  1.  4.  3.  2.  1.  0.  1.]
 [ 2.  3.  3.  4.  9.  8.  6.  0.  2.  0.]
 [ 0.  0.  3.  9. 15. 31.  6.  7.  3.  1.]
 [ 3.  0.  3. 13. 40. 35. 24. 11.  8.  1.]
 [ 0.  1.  5. 17. 49. 63. 65. 26. 14.  3.]
 [ 2.  1.  6.  8. 34. 47. 75. 33. 15.  5.]
 [ 0.  0.  1.  6. 10. 19. 37. 32. 14.  6.]
 [ 0.  0.  4.  3.  7.  9. 10. 16. 11. 11.]]


`2.` We didn't do so bad on making those predictions!  But, how many user-movie pairs were we unable to make predictions for?  Use the cell below to answer this question.

In [45]:
print("number of user-movie pairs that we were unable to predict for: ", val_df.shape[0] - len(preds))

number of user-movie pairs that we were unable to predict for:  1041


### Content Based For New Movies

If all of the above went well, you will notice we still have work to do!  We need to bring in a few things we picked up from the last lesson to use for those new users and movies.  Below is the code used to make the content based recommendations, which found movies that were similar to one another.  This was from **5_Content_Based_Recommendations** in the previous lesson.

The below function **find_similar_movies** will provide similar movies to any movie based only on content.  

Run the cell below to gain access to the content based similarity functions.

In [46]:
# Subset so movie_content is only using the dummy variables for each genre and the 3 century based year dummy columns
movie_content = np.array(movies.iloc[:,4:])

# Take the dot product to obtain a movie x movie matrix of similarities
dot_prod_movies = movie_content.dot(np.transpose(movie_content))


def find_similar_movies(movie_id):
    '''
    INPUT
    movie_id - a movie_id 
    OUTPUT
    similar_movies - an array of the most similar movies by title
    '''
    # find the row of each movie id
    movie_idx = np.where(movies['movie_id'] == movie_id)[0][0]
    
    # find the most similar movie indices - to start I said they need to be the same for all content
    similar_idxs = np.where(dot_prod_movies[movie_idx] == np.max(dot_prod_movies[movie_idx]))[0]
    
    # pull the movie titles based on the indices
    similar_movies = np.array(movies.iloc[similar_idxs, ]['movie'])
    
    return similar_movies
    
    
def get_movie_names(movie_ids):
    '''
    INPUT
    movie_ids - a list of movie_ids
    OUTPUT
    movies - a list of movie names associated with the movie_ids
    
    '''
    movie_lst = list(movies[movies['movie_id'].isin(movie_ids)]['movie'])
   
    return movie_lst

### Rank Based For New Users

From the above two code cells, we have a way to make recommendations for movie-user pairs that have ratings in any part of our user-movie matrix.  We also have a way to make ratings for movies that have never received a rating using movie similarities.

In this last part here, we need a way to make recommendations to new users.  For this, our functions from **2_Most_Popular_Recommendations** in Lesson 1 will come in handy.  Run the cell below to have these functions available.

Run the cell below to gain access to the rank based functions.

In [47]:
dot_prod_movies.shape

(31245, 31245)

In [48]:
def create_ranked_df(movies, reviews):
        '''
        INPUT
        movies - the movies dataframe
        reviews - the reviews dataframe
        
        OUTPUT
        ranked_movies - a dataframe with movies that are sorted by highest avg rating, more reviews, 
                        then time, and must have more than 4 ratings
        '''
        
        # Pull the average ratings and number of ratings for each movie
        movie_ratings = reviews.groupby('movie_id')['rating']
        avg_ratings = movie_ratings.mean()
        num_ratings = movie_ratings.count()
        last_rating = pd.DataFrame(reviews.groupby('movie_id').max()['date'])
        last_rating.columns = ['last_rating']

        # Add Dates
        rating_count_df = pd.DataFrame({'avg_rating': avg_ratings, 'num_ratings': num_ratings})
        rating_count_df = rating_count_df.join(last_rating)

        # merge with the movies dataset
        movie_recs = movies.set_index('movie_id').join(rating_count_df)

        # sort by top avg rating and number of ratings
        ranked_movies = movie_recs.sort_values(['avg_rating', 'num_ratings', 'last_rating'], ascending=False)

        # for edge cases - subset the movie list to those with only 5 or more reviews
        ranked_movies = ranked_movies[ranked_movies['num_ratings'] > 4]
        
        return ranked_movies
    

def popular_recommendations(user_id, n_top, ranked_movies):
    '''
    INPUT:
    user_id - the user_id (str) of the individual you are making recommendations for
    n_top - an integer of the number recommendations you want back
    ranked_movies - a pandas dataframe of the already ranked movies based on avg rating, count, and time

    OUTPUT:
    top_movies - a list of the n_top recommended movies by movie title in order best to worst
    '''

    top_movies = list(ranked_movies['movie'][:n_top])

    return top_movies
        

### Now For Your Task

The above cells set up everything we need to use to make predictions.  Your task is to write a function, which uses the above information as necessary to provide recommendations for every user in the **val_df** dataframe.  There isn't one right way to do this, but using a blend between the three could be your best bet.  

You can see the blended approach I used in the video on the next page, but feel free to be creative with your solution!

`3.` Use the function below along with the document strings to assist with completing the task for this notebook.  

In [58]:
movies_ranked = create_ranked_df(movies, reviews)

In [122]:
np.where(train_data_df.loc[8].isnull())[0]

array([   0,    1,    2, ..., 2676, 2677, 2678])

In [119]:
np.array(train_data_df.loc[8].index[np.where(train_data_df.loc[8].isnull())[0]])

array([   2844,    8133,   13427, ..., 2735466, 2748368, 2750600])

In [101]:
wtf1 = np.array([1,2,3,4,5])
wtf2 = np.array([5,4,3,2,1])

In [106]:
wtf2[np.argsort(wtf1)[::-1]]

array([1, 2, 3, 4, 5])

In [123]:
def make_recommendations(_id, _id_type='movie', train_data=train_data_df, 
                         train_df=train_df, movies=movies, rec_num=5,
                         user_mat=user_mat, movie_mat=movie_mat):
    '''
    INPUT:
    _id - either a user or movie id (int)
    _id_type - "movie" or "user" (str)
    train_data - dataframe of data as user-movie matrix
    train_df - dataframe of training data reviews
    movies - movies df
    rec_num - number of recommendations to return (int)
    user_mat - the U matrix of matrix factorization
    movie_mat - the V matrix of matrix factorization
    
    OUTPUT:
    rec_ids - (array) a list or numpy array of recommended movies by id                  
    rec_names - (array) a list or numpy array of recommended movies by name
    '''
    if _id_type is 'movie': # if movie type
        # get recs from similarity matrix
        self_names = np.array(get_movie_names([_id]))
        rec_names = find_similar_movies(_id)
        rec_names = np.setdiff1d(rec_names, self_names, assume_unique=True)[:rec_num]
        rec_ids = np.array([movies[movies.movie==x].iloc[0,0] for x in rec_names])
    else: # else user type
        if _id in train_data_df.index: # if user is existing
            user_id = _id
            row_data = train_data_df.loc[user_id]
            movie_ids = np.array(row_data.index[np.where(row_data.isnull())[0]])
            preds = np.array([predict_rating(user_mat, movie_mat, user_id, movie_id) for movie_id in movie_ids])
            rec_ids = movie_ids[np.argsort(preds)[::-1]][:rec_num]
            rec_names = np.array(get_movie_names(rec_ids))
            pass
        else: # new user
            rec_names = np.array(popular_recommendations(_id, rec_num, movies_ranked))
            rec_ids = np.array([movies[movies.movie==x].iloc[0,0] for x in rec_names])
            pass
    
    return rec_ids, rec_names

In [127]:
movies

movie_id                                              movie  \
0             8      Edison Kinetoscopic Record of a Sneeze (1894)   
1            10                La sortie des usines Lumière (1895)   
2            12                      The Arrival of a Train (1896)   
3            25  The Oxford and Cambridge University Boat Race ...   
4            91                         Le manoir du diable (1896)   
5           417                      Le voyage dans la lune (1902)   
6           439                     The Great Train Robbery (1903)   
7           443        Hiawatha, the Messiah of the Ojibway (1903)   
8           628                    The Adventures of Dollie (1908)   
9           833                          The Country Doctor (1909)   
10         1223                                Frankenstein (1910)   
11         1740                       The Lonedale Operator (1911)   
12         2101                                   Cleopatra (1912)   
13         2130                                   L'inferno (1911)   
14         2354        Max et Jane veulent faire du théâtre (1911)   
15         2844       Fantômas - À l'ombre de la guillotine (1913)   
16         3740                                     Cabiria (1914)   
17         3863                          Dough and Dynamite (1914)   
18         4099            His Majesty, the Scarecrow of Oz (1914)   
19         4100                          His Musical Career (1914)   
20         4101                          His New Profession (1914)   
21         4210                                Laughing Gas (1914)   
22         4395                             The New Janitor (1914)   
23         4457                    The Patchwork Girl of Oz (1914)   
24         4518                                  Recreation (1914)   
25         4546                                The Rounders (1914)   
26         4936                                    The Bank (1915)   
27         4972                       The Birth of a Nation (1915)   
28         5074                                The Champion (1915)   
29         5078                                   The Cheat (1915)   
...         ...                                                ...   
31215   7942708                            KL Special Force (2018)   
31216   7949046                                     Paradox (2018)   
31217   7959216                              Utøya 22. juli (2018)   
31218   7967954                               Lee Chong Wei (2018)   
31219   7983794                            Operation Odessa (2018)   
31220   7983844                             Take Your Pills (2018)   
31221   8005338                       Chris Rock: Tamborine (2018)   
31222   8043254                               Sirb al-Hamam (2018)   
31223   8054150    O chyom govoryat muzhchiny. Prodolzhenie (2018)   
31224   8075496                                         Bao (2018)   
31225   8079546                  Artist at Work: Annie Wood (2018)   
31226   8080268  Rock 'n' Roll Guns for Hire: The Story of the ...   
31227   8080556                   The Director and The Jedi (2018)   
31228   8088944                      Ban-deu-si Jab-neun-da (2017)   
31229   8092252                                 Be with You (2018)   
31230   8102036              Kevin Smith: Silent But Deadly (2018)   
31231   8106570                           The Rachel Divide (2018)   
31232   8119752                                   Gon-ji-am (2018)   
31233   8123286                                  Dizájneren (2016)   
31234   8140564                              My Perfect You (2018)   
31235   8144778  The Redeemed and the Dominant: Fittest on Eart...   
31236   8144868                                    Pailalim (2017)   
31237   8206708                            Carry on Jatta 2 (2018)   
31238   8289196        John McCain: For Whom the Bell Tolls (2018)   
31239   8324578            Kevin James: Never Don't Give Up (2018)   
31240   8335880  

In [129]:
# Use these cells to see that you can truly predict for everyone in the test set
# Do you see anything insightful?
for movie_id in movies.movie_id:
    print("movie_id %d" % movie_id)
    print(make_recommendations(movie_id)[1])

movie_id 8
['La sortie des usines Lumière (1895)' 'The Arrival of a Train (1896)'
 'Annabelle Serpentine Dance (1895)' 'Roundhay Garden Scene (1888)'
 'Llandudno Happy Valley and Minstrel Show (1898)']
movie_id 10
['Edison Kinetoscopic Record of a Sneeze (1894)'
 'The Arrival of a Train (1896)' 'Annabelle Serpentine Dance (1895)'
 'Roundhay Garden Scene (1888)'
 'Llandudno Happy Valley and Minstrel Show (1898)']
movie_id 12
['Edison Kinetoscopic Record of a Sneeze (1894)'
 'La sortie des usines Lumière (1895)' 'Annabelle Serpentine Dance (1895)'
 'Roundhay Garden Scene (1888)'
 'Llandudno Happy Valley and Minstrel Show (1898)']
movie_id 25
['Edison Kinetoscopic Record of a Sneeze (1894)'
 'La sortie des usines Lumière (1895)' 'The Arrival of a Train (1896)'
 'Le manoir du diable (1896)' 'The Kiss (1896)']
movie_id 91
[]
movie_id 417
['Black Angel (1980)'
 'Indiana Jones and the Temple of the Forbidden Eye (1995)']
movie_id 439
[]
movie_id 443
['Le voyage dans la lune (1902)' 'The Great

['The Lonedale Operator (1911)'
 'Broken Blossoms or The Yellow Man and the Girl (1919)'
 'True Heart Susie (1919)' 'Way Down East (1920)'
 'The Hunchback of Notre Dame (1923)']
movie_id 12224
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 12278
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 12349
['The Kid Brother (1927)' 'Skippy (1931)' 'Anne of Green Gables (1934)'
 'Bright Eyes (1934)' 'Rebecca of Sunnybrook Farm (1938)']
movie_id 12364
['Faust - Eine deutsche Volkssage (1926)' 'Werewolf of London (1935)'
 "Dracula's Daughter (1936)" 'The Wolf Man (1941)'
 'The Picture of Dorian Gray (1945)']
movie_id 12494
['La Mary (1974)' 'Die tödliche Maria (1993)' 'In Dreams (1999)']
movie_id 12532
['Cleopatra (1912)' 'Cabiria (1914)' 'The Birth of a Nation (191

['Häxan (1922)' 'Nanook of the North (1922)'
 'Chelovek s kino-apparatom (1929)' 'Drifters (1929)'
 'À propos de Nice (1930)']
movie_id 17729
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 17739
['The Cat and the Canary (1939)' 'The Ghost Breakers (1940)'
 'Abbott and Costello Meet the Killer, Boris Karloff (1949)'
 'Abbott and Costello Meet Dr. Jekyll and Mr. Hyde (1953)'
 'Tales of Terror (1962)']
movie_id 17765
['Slap Shot (1977)' 'Breaking Away (1979)' 'North Dallas Forty (1979)'
 'Oxford Blues (1984)' 'The Best of Times (1986)']
movie_id 17825
['Le salaire de la peur (1953)' 'Seven Waves Away (1957)'
 "The Devil at 4 O'Clock (1961)" 'Lord of the Flies (1963)'
 'The Naked Prey (1965)']
movie_id 17836
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 178

['The Lonedale Operator (1911)'
 'Broken Blossoms or The Yellow Man and the Girl (1919)'
 'True Heart Susie (1919)' 'Way Down East (1920)'
 'Within Our Gates (1920)']
movie_id 19993
['The Jazz Singer (1927)' 'The Broadway Melody (1929)'
 'The Cocoanuts (1929)' 'The Love Parade (1929)' 'Animal Crackers (1930)']
movie_id 19999
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 20030
['Cabiria (1914)' 'Mutiny on the Bounty (1935)'
 'For Whom the Bell Tolls (1943)' 'Samson and Delilah (1949)'
 'Ivanhoe (1952)']
movie_id 20112
['Horse Feathers (1932)' 'Love Me Tonight (1932)'
 'One Hour with You (1932)' 'Dancing Lady (1933)'
 'Footlight Parade (1933)']
movie_id 20122
['The Lonedale Operator (1911)'
 'Broken Blossoms or The Yellow Man and the Girl (1919)'
 'True Heart Susie (1919)' 'Way Down East (1920)'
 'Within Our Gates (1920)']
movie_id 20142
['The Lonedale Operator (1911)'
 

['Die Büchse der Pandora (1929)' 'The Big House (1930)'
 'Three on a Match (1932)' 'Hijôsen no onna (1933)'
 'Manhattan Melodrama (1934)']
movie_id 21890
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 22017
['The Country Doctor (1909)' 'The Lonedale Operator (1911)'
 'Cleopatra (1912)' "L'inferno (1911)"
 "Fantômas - À l'ombre de la guillotine (1913)"]
movie_id 22048
['Behind the Screen (1916)' 'The Vagabond (1916)'
 'True Heart Susie (1919)' 'Neighbors (1920)' 'Seven Chances (1925)']
movie_id 22058
['Max et Jane veulent faire du théâtre (1911)' 'Dough and Dynamite (1914)'
 'His Musical Career (1914)' 'His New Profession (1914)'
 'Laughing Gas (1914)']
movie_id 22080
['The Lonedale Operator (1911)'
 'Broken Blossoms or The Yellow Man and the Girl (1919)'
 'True Heart Susie (1919)' 'Way Down East (1920)'
 'Within Our Gates (1920)']
movie_id 22100
['The Crimes of Stephen 

...

['Critters: Bounty Hunter (2014)' 'Pyotr495 (2016)'
 'Prologue: Last Supper (2017)' 'Zygote (2017)']
movie_id 6992058
['Scratch (2001)' 'Condo Painting (2000)'
 'Keep the River on Your Right: A Modern Cannibal Tale (2000)'
 'A Galaxy Far, Far Away (2001)' 'Dark Days (2000)']
movie_id 6996016
['Kate & Leopold (2001)' 'Return to Me (2000)' 'Heartbreakers (2001)'
 'Intolerable Cruelty (2003)' 'It Had to Be You (2000)']
movie_id 6998626
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7006426
['Kate & Leopold (2001)' "Don's Plum (2001)" 'State and Main (2000)'
 'Sånger från andra våningen (2000)' 'Chicken Run (2000)']
movie_id 7010412
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7012864
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7013286
['Children on Th

['From Hell (2001)' 'Supernova (2000)' 'Lost Souls (2000)'
 'Cherry Falls (2000)' 'Anatomie (2000)']
movie_id 7160070
['Avalon (2001)' 'D-War (2007)' 'Wu ji (2005)' 'Ye yan (2006)'
 'Dracula Untold (2014)']
movie_id 7162324
['Burma VJ: Reporter i et lukket land (2008)' 'Farmageddon (2011)'
 'Overdos (2010)' 'Fresh (2009)' 'Food Stamped (2010)']
movie_id 7164714
['A Galaxy Far, Far Away (2001)' 'The Original Kings of Comedy (2000)'
 "Dave Chappelle: Killin' Them Softly (2000)"
 'George Carlin: Complaints &amp; Grievances (2001)'
 'Notorious C.H.O. (2002)']
movie_id 7166310
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7180392
['The Manson Family (2003)' 'Vulgar (2000)' 'Heartbreakers (2001)'
 'The Crow: Salvation (2000)' 'Cement (2000)']
movie_id 7180544
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7184744
['Kate & Leopold (2001

['Scratch (2001)' 'Condo Painting (2000)'
 'Keep the River on Your Right: A Modern Cannibal Tale (2000)'
 'A Galaxy Far, Far Away (2001)' 'Dark Days (2000)']
movie_id 7329858
['From Hell (2001)' 'Scream 3 (2000)' 'D-Tox (2002)'
 'What Lies Beneath (2000)' 'Cherry Falls (2000)']
movie_id 7332500
['Scratch (2001)' 'Condo Painting (2000)'
 'Keep the River on Your Right: A Modern Cannibal Tale (2000)'
 'A Galaxy Far, Far Away (2001)' 'Dark Days (2000)']
movie_id 7336012
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7339826
['The Tigger Movie (2000)' 'Otesánek (2000)' 'Waking Life (2001)'
 'Eight Crazy Nights (2002)' 'Les triplettes de Belleville (2003)']
movie_id 7341406
['The Million Dollar Hotel (2000)' 'Enigma (2001)'
 'What Lies Beneath (2000)' 'The In Crowd (2000)' 'Mulholland Dr. (2001)']
movie_id 7342204
["Don's Plum (2001)" 'State and Main (2000)'
 'Sånger från andra våningen (2000)' 'Return to Me (2000

['180° South (2010)' 'Manny (2014)' 'Pelotero (2011)'
 'The Four Year Plan (2011)' 'Happy Valley (2014)']
movie_id 7583280
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)']
movie_id 7588584
['Scratch (2001)' 'The Filth and the Fury (2000)' 'Calle 54 (2000)'
 '1 Giant Leap (2002)' 'Standing in the Shadows of Motown (2002)']
movie_id 7588752
['Scratch (2001)' 'Condo Painting (2000)'
 'Keep the River on Your Right: A Modern Cannibal Tale (2000)'
 'A Galaxy Far, Far Away (2001)' 'Dark Days (2000)']
movie_id 7588790
['Scratch (2001)' 'Condo Painting (2000)'
 'Keep the River on Your Right: A Modern Cannibal Tale (2000)'
 'A Galaxy Far, Far Away (2001)' 'Dark Days (2000)']
movie_id 7597454
['D-Tox (2002)' 'Bless the Child (2000)' 'Bones (2001)'
 'Subconscious Cruelty (2000)' 'The Watcher (2000)']
movie_id 7599050
['What Is It? (2005)' 'Glitter (2001)' 'Fa yeung nin wa (2000)'
 'The Manson Family (2003)' 'Chinese Coffee (2000)'

['John Henry (2000)' '7:35 de la mañana (2003)' 'Marry the Night (2011)'
 'Donner Party: The Musical (2013)' 'Once Upon a Mime (2013)']
movie_id 7871636
['Kate & Leopold (2001)' "Don's Plum (2001)" 'State and Main (2000)'
 'Sånger från andra våningen (2000)' 'Chicken Run (2000)']
movie_id 7875626
['Kate & Leopold (2001)' 'What Is It? (2005)' 'Glitter (2001)'
 'Fa yeung nin wa (2000)' 'The Manson Family (2003)']
movie_id 7875948
['From Hell (2001)' 'Resident Evil (2002)' 'Scream 3 (2000)'
 'Pitch Black (2000)' 'Supernova (2000)']
movie_id 7879350
['Polustanok (2000)' 'Deep Sea (2006)' 'Forza Bastia (2002)'
 'Roving Mars (2006)' 'Phantom Limb (2005)']
movie_id 7882406
['Kate & Leopold (2001)' 'What Is It? (2005)' 'Glitter (2001)'
 'Fa yeung nin wa (2000)' 'The Manson Family (2003)']
movie_id 7887532
['Hitch (2000)' 'John Henry (2000)' 'Outer Space (2000)' 'Rejected (2000)'
 'Thumbtanic (2000)']
movie_id 7888178
['Kate & Leopold (2001)' 'What Is It? (2005)' 'Glitter (2001)'
 'Fa yeung nin

In [130]:
for user_id in np.unique(val_df.user_id):
    print("user_id %d" % user_id)
    print(make_recommendations(user_id, _id_type='user')[1])

user_id 66
['Empire of the Sun (1987)' 'Blood Diamond (2006)' 'Life of Pi (2012)'
 'Amour (2012)' 'Django Unchained (2012)']
user_id 90
["Schindler's List (1993)" 'Blood Diamond (2006)'
 'Silver Linings Playbook (2012)' 'The Sapphires (2012)'
 'Zero Dark Thirty (2012)']
user_id 112
['A Few Good Men (1992)' 'Casino (1995)'
 'The Curious Case of Benjamin Button (2008)' 'The Wrestler (2008)'
 'Incendies (2010)']
user_id 219
['The Shawshank Redemption (1994)' 'The Green Mile (1999)' 'Amélie (2001)'
 'Blood Diamond (2006)' 'Silver Linings Playbook (2012)']
user_id 220
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 292
['The Godfather (1972)' 'Empire of the Sun (1987)' 'Pulp Fiction (1994)'
 'Blood Diamond (2006)' 'The Dark Knight (2008)']
user_id 298
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Se

['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 2719
['Empire of the Sun (1987)' 'The Shawshank Redemption (1994)'
 'Blood Diamond (2006)' 'The Hobbit: An Unexpected Journey (2012)'
 'Lo imposible (2012)']
user_id 2793
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 2797
['The Shawshank Redemption (1994)' 'Memento (2000)'
 'The Curious Case of Benjamin Button (2008)' 'Incendies (2010)'
 'Shame (2011)']
user_id 2854
['As Good as It Gets (1997)' 'Argo (2012)'
 'Silver Linings Playbook (2012)' 'The Sapphires (2012)' 'Bad 25 (2012)']
user_id 2916
['Empire of the Sun (1987)' 'Casino (1995)' 'Blood Diamond (2006)'
 'Step Brothers (2008)' 'Django Unchained (2012)']
user_id 2919
['Empire of the Sun (1987)' 'The Curious

['Empire of the Sun (1987)' 'Blood Diamond (2006)' 'Incendies (2010)'
 'The Sapphires (2012)' 'Shame (2011)']
user_id 4698
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 4711
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 4719
['Empire of the Sun (1987)' 'Silver Linings Playbook (2012)'
 'Django Unchained (2012)' 'Jagten (2012)' 'Paperman (2012)']
user_id 4770
['Empire of the Sun (1987)' 'Casino (1995)' 'Argo (2012)'
 'Oz the Great and Powerful (2013)'
 'The Perks of Being a Wallflower (2012)']
user_id 4791
['Empire of the Sun (1987)' 'Pulp Fiction (1994)'
 'Saving Private Ryan (1998)' 'Blood Diamond (2006)'
 'The Dark Knight (2008)']
user_id 4820
['Empire of the Sun (1987)' 'The Hobbit: An Unexpected Journey

['Empire of the Sun (1987)' 'Casino (1995)' 'Incendies (2010)'
 'Oz the Great and Powerful (2013)' 'Django Unchained (2012)']
user_id 6926
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 7129
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 7136
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 7162
['Empire of the Sun (1987)' 'The Curious Case of Benjamin Button (2008)'
 'Blood Diamond (2006)' 'There Will Be Blood (2007)'
 'Django Unchained (2012)']
user_id 7215
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'


['Empire of the Sun (1987)' 'Silver Linings Playbook (2012)'
 'The Perks of Being a Wallflower (2012)' 'Django Unchained (2012)'
 'Beasts of the Southern Wild (2012)']
user_id 9034
['Empire of the Sun (1987)' 'Memento (2000)' 'Life of Pi (2012)'
 'The Fall (2006)' 'Shame (2011)']
user_id 9043
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 9104
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 9109
['The Lion King (1994)' 'The Fall (2006)'
 'The Perks of Being a Wallflower (2012)' 'Shame (2011)'
 'Django Unchained (2012)']
user_id 9239
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]


...

['Life of Pi (2012)' 'Argo (2012)' 'Silver Linings Playbook (2012)'
 'Incendies (2010)' 'Django Unchained (2012)']
user_id 43305
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 43369
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 43370
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 43386
['Snitch (2013)' 'The Hobbit: An Unexpected Journey (2012)' 'Argo (2012)'
 'Silver Linings Playbook (2012)' 'Django Unchained (2012)']
user_id 43408
['Empire of the Sun (1987)' 'Argo (2012)' 'Shame (2011)'
 'Django Unchained (2012)' 'Jagten (2012)']
user_id 43484
['MSG 2 the Messenger (20

['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 45634
['Empire of the Sun (1987)' 'The Shawshank Redemption (1994)'
 'Incendies (2010)' 'Shame (2011)' 'Wreck-It Ralph (2012)']
user_id 45650
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 45718
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 45969
['Empire of the Sun (1987)' 'Life of Pi (2012)' 'Argo (2012)'
 'Gran Torino (2008)' 'Incendies (2010)']
user_id 45986
['Empire of the Sun (1987)' 'The Shawshank Redemption (1994)'
 'Blood Diamond (2006)' 'Silver Linings Playbook (2012)'
 'Django Unchained (2012)']
user_id 46014
['E

['Empire of the Sun (1987)' 'Blood Diamond (2006)' 'The Fall (2006)'
 'The Sapphires (2012)' 'Shame (2011)']
user_id 47821
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 47826
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 47848
['Empire of the Sun (1987)' 'The Hobbit: An Unexpected Journey (2012)'
 'Argo (2012)' 'Silver Linings Playbook (2012)'
 'The Perks of Being a Wallflower (2012)']
user_id 47884
['Empire of the Sun (1987)' 'The Curious Case of Benjamin Button (2008)'
 'Life of Pi (2012)' 'Silver Linings Playbook (2012)'
 'Beasts of the Southern Wild (2012)']
user_id 47909
['As Good as It Gets (1997)' 'Lincoln (2012)' 'The Last Mimzy (2007)'
 'The Avengers (2012)' 'Wreck-It Ralph (2012)']
user_id 47964
[

['The Shawshank Redemption (1994)' 'Blood Diamond (2006)'
 'Life of Pi (2012)' 'The Hobbit: An Unexpected Journey (2012)'
 'Django Unchained (2012)']
user_id 50235
['Empire of the Sun (1987)' 'Blood Diamond (2006)' 'Incendies (2010)'
 'Oz the Great and Powerful (2013)' 'Django Unchained (2012)']
user_id 50249
['Empire of the Sun (1987)' 'Moulin Rouge! (2001)' 'Memento (2000)'
 'Skyfall (2012)' 'Shame (2011)']
user_id 50267
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 50344
['Psycho (1960)' 'Empire of the Sun (1987)' 'Fight Club (1999)'
 'The Perks of Being a Wallflower (2012)' 'Shame (2011)']
user_id 50361
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 50380
['MSG 2 the Messenger (2015)' 'Avengers: Age of U

['Empire of the Sun (1987)' "Schindler's List (1993)"
 'Blood Diamond (2006)' 'Gran Torino (2008)' 'Incendies (2010)']
user_id 52466
['Psycho (1960)' 'Empire of the Sun (1987)' 'De reis van Chihiro (2001)'
 'Life of Pi (2012)' 'Sound City (2013)']
user_id 52488
['Empire of the Sun (1987)' 'Casino (1995)'
 'The Hobbit: An Unexpected Journey (2012)' 'Gran Torino (2008)'
 'Django Unchained (2012)']
user_id 52505
['Empire of the Sun (1987)' 'Blood Diamond (2006)'
 'Oz the Great and Powerful (2013)' 'Wreck-It Ralph (2012)'
 'Django Unchained (2012)']
user_id 52583
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 52603
['MSG 2 the Messenger (2015)' 'Avengers: Age of Ultron Parody (2015)'
 'Sorry to Bother You (2018)' 'Selam (2013)'
 "Quiet Riot: Well Now You're Here, There's No Way Back (2014)"]
user_id 52663
['Empire of the Sun (1987)' 'De reis van Chihi

**Use this cell to discuss your findings.**